## **Trabalho Prático Final de NLP**
### **Etapa 1: Download e Pré-processamento da Legislação**
**Professores:** André Carvalho e Altigran da Silva

**Alunos:**

Bianka Vasconcelos

Girlana Souza

Ricardo Bonfim

**Descrição do Trabalho:** Este trabalho consiste em desenvolver uma LLM que responda perguntas sobre a legislação acadêmica da UFAM. O trabalho envolve o download e pré-processamento dos documentos da legislação, a criação de uma base de dados sintética de instruções, o treinamento do modelo usando técnicas de LoRA/QLoRA, e a implementação de um sistema de RAG (Retrieval-Augmented Generation) para fornecer respostas precisas baseadas nos documentos da legislação.

### **Objetivo:** Neste notebook, iremos fazer a extração dos textos dos documentos PDF's disponibilizados em: https://proeg.ufam.edu.br/normas-academicas/57-proeg/146-legislacao-e-normas.html. Com isso, poderemos usar o texto desses documentos para criar a base sintética de instruções, e dessa forma, será possível fazer o fine tuning.

### **Configurando o ambiente**

Primeiro, vamos começar com algumas instalações e importações básicas para configurar o ambiente.

In [ ]:
!pip install pytesseract
!pip install pdf2image
!pip install pillow
!pip install requests
!pip install tempfile
!pip install tdqm
!apt-get install poppler-utils
!apt-get install tesseract-ocr

ERROR: Could not find a version that satisfies the requirement tempfile (from versions: none)
ERROR: No matching distribution found for tempfile
  Preparing metadata (setup.py) ... done
  Created wheel for tdqm: filename=tdqm-0.0.1-py3-none-any.whl size=1321 sha256=eda8ad197c3c248d5e5a74dbbf56afffb8060b3c43d35d962221e07eba35cf54
  Stored in directory: /root/.cache/pip/wheels/37/31/b8/7b711038035720ba0df14376af06e5e76b9bd61759c861ad92
Successfully built tdqm
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following NEW packages will be installed:
  poppler-utils
0 upgraded, 1 newly installed, 0 to remove and 45 not upgraded.
Need to get 186 kB of archives.
After this operation, 696 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 poppler-utils amd64 22.02.0-2ubuntu0.5 [186 kB]
Fetched 186 kB in 1s (185 kB/s)
Selecting previously unselected package poppler-utils.
(Reading databas

In [ ]:
import os, re
import platform
import requests
import pytesseract
import urllib.request # para importar o arquivo da Tiny Shakespeare
import unicodedata
from tqdm.notebook import tqdm

from tempfile import TemporaryDirectory
from pathlib import Path
from pdf2image import convert_from_path
from PIL import Image
from tqdm import tqdm
from nltk.metrics.distance import edit_distance # para calcular a distancia de levenstrein

#### **Pré Processamento**

A linguagem python é muito usada para análise de dados, mas às vezes os dados não estão em um formato conveniente para trabalhar (em formato de texto). Para resolver isso, convertemos arquivos como PDFs ou imagens para texto. Python possui várias bibliotecas para essa tarefa, como PyPDF2. No entanto, uma desvantagem é que PDFs podem usar diferentes codificações, como UTF-8 ou ASCII, o que pode causar perda de dados na conversão. Para evitar isso, podemos converter as páginas do PDF em imagens e depois usar **OCR** (Reconhecimento Óptico de Caracteres) para extrair e armazenar o texto das imagens em um arquivo de texto.

Portanto, usaremos as ferramentas do `OCR` para extrair o texto dos documentos.

Fonte de auxílio: https://www.geeksforgeeks.org/python-reading-contents-of-pdf-using-ocr-optical-character-recognition/

Para conseguir extrair o texto dos documentos, optamos em baixá-los localmente, deixando salvos em uma pasta do google drive. Portanto, abaixo temos alguns comandos para fazer conexão com o drive para acessar tais documentos.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


Abaixo, vamos configurar as variáveis globais e os diretórios para acessar os arquivos.

In [ ]:
# HOME = os.path.join(os.getcwd(), "Documentos da base") # roda local
# print(HOME)
HOME = "/content/drive/MyDrive/NLP-2024-1/TP3 (Final)/Documentos da base" # diretório principal dos documentos HOME
FOLDER_TEXT = os.path.join(HOME, "Arquivos de texto") # onde os documentos serão salvos

if not os.path.exists(FOLDER_TEXT):
	os.makedirs(FOLDER_TEXT)

temp_pdf_path = os.path.join(HOME, "temp.pdf")
out_directory = Path(FOLDER_TEXT)

#### **Convertendo o PDF para Imagem**

Desenvolvemos uma função que faz a primeira etapa do OCR, convertendo um arquivo PDF para um arquivo de imagem (.jpg). Ela converte cada página de um PDF em uma imagem JPEG de alta qualidade e salva essas imagens em um diretório temporário. Com isso, gera-se uma lista com os caminhos das imagens e usamos uma barra de progresso para mostrar o andamento da conversão, com auxílio da biblioteca `tqdm`.

In [ ]:
def pdf2jpeg(tempdir, pdf_file, image_file_list):
    """
    Etapa #1 : Convertendo PDF para imagens
    """

    pdf_pages = convert_from_path(pdf_file, 500) # páginas do pdf são convertidas

    # percorrer todas as páginas convertidas para imagem
    for page_enumeration, page in enumerate(tqdm(pdf_pages, desc="Páginas convertidas"), start=1):

        # criar e salvar a imagem
        filename = f"{tempdir}/page_{page_enumeration:03}.jpg"

        page.save(filename, "JPEG")
        image_file_list.append(filename)

#### **Convertendo a Imagem para Texto**

A função abaixo é responsável pela próxima etapa do OCR, que é converter o texto de uma imagem para um arquivo txt. A ideia é percorrer cada imagem e usar a biblioteca `pytesseract` para reconhecer e extrair texto de cada imagem. Durante o processamento , removemos quebras de linha causadas por palavras divididas com hífen (-) no final da linha.

Ao fim do processo, a função adiciona o texto processado ao arquivo de saída e imprime o nome do arquivo salvo.

In [ ]:
def jpeg2txt(file_name, image_file_list, out_directory):
    """
    Etapa #2 - Reconhecer textos de imagem com OCR
    """
    if ".PDF" in file_name:
        text_name = file_name.replace(".PDF", ".txt")
    elif ".pdf" in file_name:
        text_name = file_name.replace(".pdf", ".txt")
    text_file = os.path.join(out_directory, text_name)

    with open(text_file, "a", encoding="utf-8") as output_file:
        for image_file in tqdm(image_file_list, desc="Processando imagens"):

            text = str(((pytesseract.image_to_string(Image.open(image_file)))))

            text = text.replace("-\n", "")

            output_file.write(text)

        print("Arquivo salvo como: ", text_name)
        print()

#### **Hora de Converter**

A função abaixo irá chamar todas as que foram anteriormente desenvolvidas.
- Primeiro, ela cria uma lista de todos os arquivos no diretório HOME.
- Depois, para cada arquivo PDF encontrado, define-se o nome do arquivo de texto correspondente (.txt).
- Se o arquivo de texto ainda não existir no diretório de saída (out_directory), inicia o processamento.
- Cria um diretório temporário para armazenar imagens das páginas do PDF.
- Usa a função `pdf2jpeg` para converter o PDF em imagens JPEG e armazena os nomes das imagens na lista *image_file_list*.
- Usa a função `jpeg2txt` para extrair texto das imagens JPEG e salvar no arquivo de texto correspondente.

Portanto, tal função serve para automatizar a conversão de PDFs em texto, criando imagens das páginas e depois extraindo o texto dessas imagens.

In [ ]:
def pdf2file():
	# Seleção do PDF
	cont = 0
	files = [x for x in os.listdir(HOME) if os.path.isfile(os.path.join(HOME, x))]
	for nome_arquivo in files:

		# uma verificação adicional em caso de erro em arquivos de nome com '.PDF' (maiúsculo)
		if ".PDF" in nome_arquivo:
			text_name = nome_arquivo.replace(".PDF", ".txt")
		elif ".pdf" in nome_arquivo:
			text_name = nome_arquivo.replace(".pdf", ".txt")

		if not os.path.exists(os.path.join(out_directory, text_name)):

			print("#" * 20, f'CONVERTING THE FILE: {nome_arquivo}',"#" * 20)
			# as páginas do PDF ficam nessa lista
			image_file_list = []

			PDF_path = os.path.join(HOME, nome_arquivo) # pega o caminho do pdf

			# download_pdf(PDF_url, temp_pdf_path)

			with TemporaryDirectory() as tempdir:
				# cria um diretório temporário para armazenar as imagens temporárias

				pdf2jpeg(tempdir, PDF_path, image_file_list) # converte para imagem

				jpeg2txt(nome_arquivo, image_file_list, out_directory) # converte para texto




In [ ]:
pdf2file()

### **Aplicação da Distância de Levenstrein**

A OCR, apesar de muito útil para converter os PDF's para texto, ocorrem muitos erros de codificação ao longo da tradução. Portanto, alguma técnica de correção de texto é necessária para resolver esse problema, caso contrário, o modelo treinado com o fine tunning erraria muitos termos na sua resposta.

Encontramos um dicionário com todas as palavras da língua portuguesa, e optamos por utilizá-lo para nos auxiliar a corrigir o texto. Além disso, aplicamos o algoritmo da distância de edição, que compara duas palavras e fornece a distância léxica entre elas.

Utilizamos como fonte de referência: https://www.google.com/url?q=https%3A%2F%2Fmedium.com%2Fproductmanagerslife%2Fa-dist%25C3%25A2ncia-de-levenshtein-usando-a-dist%25C3%25A2ncia-entre-palavras-para-encontrar-tesouros-0edf95eb5d63

#### **Carregando o dicionário da língua portuguesa**
Primeiramente, vamos carrregar o dicionário. Ele se encontra nessa url: https://www.ime.usp.br/~pf/dicios/br-utf8.txt.

A função abaixo realiza o carregamento do dicionário, com cada linha sendo uma palavra da língua portuguesa.

In [ ]:
def carrega_dict(url):
  # nome do arquivo que ficará salvo no ambiente local
  nome_arquivo = "dicionario-pt.txt"

  # execução do download
  urllib.request.urlretrieve(url, nome_arquivo)

  # abrindo o arquivo e salvando em 'linhas_arquivo'
  linhas_arquivo = open("dicionario-pt.txt", 'r', encoding='utf-8').read()

  return linhas_arquivo

Agora, passamos a URL como parâmetro para a função e salvamos as palavras na variável dicionário.

In [ ]:
url = "https://www.ime.usp.br/~pf/dicios/br-utf8.txt"
linhas_arquivo = carrega_dict(url) # carregando a base
dicionario = linhas_arquivo.split("\n") # separando as palavras

Foi necessário incluir algumas palavras específicas que não estavam no dicionário. A forma mais simples que encontramos de fazer isso foi adicionar as palavras manualmente. Segue abaixo a adição de termos extras no dicionário.

In [ ]:
termos_extras = [
    # estados
    "acre", "alagoas", "amapá", "amazonas", "bahia", "ceará", "distrito federal", "espírito santo",
    "goiás", "maranhão", "mato grosso", "mato grosso do sul", "minas gerais", "pará", "paraíba",
    "paraná", "pernambuco", "piauí", "rio de janeiro", "rio grande do norte", "rio grande do sul",
    "rondônia", "roraima", "santa catarina", "são paulo", "sergipe", "tocantins",

    # cidades
    "abadia de goiás", "abaetetuba", "acrelândia", "açu", "aparecida de goiânia", "araraquara",
    "barretos", "barrocas", "bauru", "belo horizonte", "belo jardim", "blumenau", "boa vista",
    "boa vista do sul", "bragança paulista", "campina grande", "campinas", "campo grande",
    "canoas", "caruaru", "catalão", "ceilândia", "chapecó", "colatina", "contagem", "cruz das almas",
    "curitiba", "diadema", "divinópolis", "duque de caxias", "eunápolis", "feira de santana",
    "florianópolis", "formosa", "fortaleza", "francisco morato", "goiânia", "guarapuava",
    "guarulhos", "imperatriz", "ipatinga", "itabuna", "itajaí", "joinville", "jundiaí", "lajeado",
    "londrina", "macapá", "maceió", "manaus", "marabá", "marília", "mauá", "mogi das cruzes",
    "montes claros", "natal", "niterói", "nova iguaçu", "olinda", "ourinhos", "palmas", "parauapebas",
    "passo fundo", "pelotas", "petrópolis", "porto alegre", "porto seguro", "recife", "ribeirão preto",
    "rio branco", "rio das ostras", "salvador", "são bernardo do campo", "são caetano do sul",
    "são joão nepomuceno", "são josé", "são luís", "são paulo", "sorocaba", "taubaté", "teixeira de freitas",
    "teresina", "uberaba", "uberlândia", "umuarama", "varginha", "vitória", "volta redonda",

    # termos legislativos
    "ação civil pública", "ação direta de inconstitucionalidade", "ação penal", "aditivo contratual",
    "agente político", "audiência pública", "bancada", "caducidade", "cautelar", "código de processo civil",
    "código penal", "conselho de ética", "contraposição", "deliberação", "desenquadramento", "direito administrativo",
    "direito constitucional", "direito penal", "emenda constitucional", "estatuto", "feito", "fiscalização",
    "improbidade administrativa", "inconstitucionalidade", "intervenção federal", "jurisprudência", "legislação ordinária",
    "medida provisória", "norma jurídica", "parlamentar", "poder executivo", "poder legislativo", "poder judiciário",
    "presidência", "promulgação", "recurso especial", "reforma legislativa", "regimento interno", "sanção", "supremo tribunal federal",
    "tribunal de contas", "vacância", "veto", "votação", "liderança", "subsídio", "reversão", "regulamentação",
    "normas de procedimento", "edital", "regime de urgência", "processo legislativo", "petição inicial", "substitutivo",
    "requerimento", "relatório de comissão", "desdobramento", "decreto-lei", "ente federativo", "obrigações administrativas",
    "tributação", "recurso ordinário", "mandado de segurança", "reparação", "direitos fundamentais", "transparência",
    "governança", "compensação fiscal", "paridade", "regime jurídico", "autonomia", "direito administrativo sancionador",
    "conselho nacional", "conselho superior", "ato administrativo", "procedimento administrativo", "regime de previdência",
    "subvenção", "licitação", "concessão", "permissão", "prerrogativa", "decadência", "transição legislativa",

    # órgãos educacionais e importantes do amazonas
    "universidade federal do amazonas", "ufam",
    "instituto federal do amazonas", "ifam",
    "secretaria de estado de educação e desporto", "seduc-am",
    "fundação universidade do estado do amazonas", "uea",
    "escola superior de tecnologia",
    "centro de educação tecnológica do amazonas", "cetam",
    "instituto de ciências exatas e tecnologia", "icet",
    "centro de educação a distância", "ced",
    "faculdade de educação",
    "faculdade de tecnologia da informação",
    "faculdade de ciências agrárias",
    "faculdade de ciências da saúde",
    "escola normal superior",
    "faculdade de direito",
    "faculdade de ciências sociais",
    "sabemi", "fundação",
    "avenida rodrigo otávio", "avenida", "rodrigo", "otávio",

    "susep",
    "ans", "anvisa",
    "incra", "ibama",

     # CNPJ e outras siglas importantes
    "cnpj", "cadastro nacional de pessoa jurídica",
    "mei", "microempreendedor individual",
    "me", "microempresa",
    "eireli", "empresa individual de responsabilidade limitada",
    "ltda", "limitada",
    "cnae", "classificação nacional de atividades econômicas",
    "cpf", "cadastro de pessoas físicas",
    "inss", "instituto nacional do seguro social",
    "das", "documento de arrecadação do simples nacional",
    "dasn-simei", "declaração anual do simples nacional do mei",
    "rais", "relação anual de informações sociais",
    "nf-e", "nota fiscal eletrônica",
    "rfb", "receita federal do brasil"
]
# adicionando no dicionário
for termo in termos_extras:
    dicionario.append(termo)

#### **Correção dos Textos**

Agora, vamos iniciar o processo de correção dos textos. Primeiro, vamos definir algumas funções auxiliares que serão úteis para corrigir as palavras.

A função `limpa_palavra` recebe uma palavra como entrada e remove todos os caracteres que não são letras, números ou espaços. Ela utiliza uma expressão regular para filtrar os caracteres indesejados e, em seguida, remove quaisquer espaços em branco extras no início e no final da string. O resultado é uma palavra "limpa", que pode ser utilizada para comparação ou análise.

A `tem_acento` procura por um acento na palavra, para lidar com os acentos na prioridade de distância de edição, caso as distâncias sejam iguais.

In [ ]:
def limpar_palavra(palavra):
    # Remove pontuação e caracteres especiais, mantendo apenas letras e números
    palavra = re.sub(r'[^\w\s.]', '', palavra)
    # Remove espaços extras
    palavra = palavra.strip()
    return palavra

def tem_acento(palavra):
    return any(char in 'áéíóúâêîôûãõàç' for char in palavra)

def diferenca_acento(palavra1, palavra2):
    acentos = 'áéíóúâêîôûãõàç'
    diferenca = 0
    for char1, char2 in zip(palavra1, palavra2):
        if char1 in acentos and char2 not in acentos:
            diferenca += 1
        elif char1 not in acentos and char2 in acentos:
            diferenca += 1
    return diferenca

Agora, vamos abaixo temos a implementação da distância de Levenstrein. Feita com base no site mencionado anteriormente.

Vale ressaltar que adicionamos uma função de normalização, para que ele considere que na situação com duas palavras em que a única diferença é o acento, a palavra com o acento será considerada correta e de menor distância.

In [ ]:
def normalize_text(text):
    # remover acentuação e normalizar o texto para comparação
    return unicodedata.normalize('NFD', text).encode('ASCII', 'ignore').decode('ASCII')

def levenshtein_distance(str1, str2):
    # normalizar as srings tirando a acentuação para verificar a distância
    str1 = normalize_text(str1)
    str2 = normalize_text(str2)

    len_str1, len_str2 = len(str1), len(str2)
    matrix = [[0] * (len_str2 + 1) for _ in range(len_str1 + 1)]

    for i in range(len_str1 + 1):
        for j in range(len_str2 + 1):
            if i == 0:
                matrix[i][j] = j
            elif j == 0:
                matrix[i][j] = i
            elif str1[i - 1] == str2[j - 1]:
                matrix[i][j] = matrix[i - 1][j - 1]
            else:
                matrix[i][j] = 1 + min(matrix[i - 1][j],      # Deleção
                                       matrix[i][j - 1],      # Inserção
                                       matrix[i - 1][j - 1])  # Substituição

    return matrix[len_str1][len_str2]

Agora, a função abaixo é a que de fato irá chamar a distância de edição e as demais funções auxiliares. Seu objetivo é corrigir as palavras dos documentos de texto da legislação da UFAM, que não estão presentes no dicionário fornecido pois possem algum erro gramatical.

A função toma como parâmetros:

- `documento` (str): Caminho para o arquivo de texto que será corrigido.
- `dicionario` (list): Lista de palavras corretas usadas como referência.
- `limite_distancia` (int): Valor máximo da distância de Levenshtein permitido -para considerar uma palavra como uma possível correção.

Seu funcionamento consiste no seguinte:

- Para cada linha, verifica e processa cada palavra.
- Remove pontuação e converte a palavra para minúsculas.
- Se a palavra tem 5 ou mais caracteres e não é um número, verifica se não está no dicionário.
- Calcula a distância de Levenshtein entre a palavra e as palavras no dicionário que começam com a mesma letra e têm o mesmo comprimento.
- Seleciona a palavra do dicionário mais próxima, priorizando palavras com acentuação, se houver candidatos.
- Substitui palavras incorretas pelas corrigidas.
- Preserva a estrutura original do texto, como pontuação e espaçamento.
- Salva o texto corrigido em um novo arquivo com o sufixo _corrigido.

Segue a função de correção logo abaixo.

In [ ]:
def corrige_texto(documento, dicionario, limite_distancia):

    dicionario_set = set(dicionario)
    diretorio_saida = 'Arquivos de texto corrigidos'
    diretorio_saida_caminho = os.path.join(HOME, diretorio_saida)
    if not os.path.exists(diretorio_saida_caminho):
        os.makedirs(diretorio_saida_caminho)

    with open(documento, 'r', encoding='utf-8') as arquivo:
        linhas = arquivo.readlines()

    linhas_corrigidas = []

    for linha in tqdm(linhas, desc="Processando linhas"):
        if linha == '\n':
            linhas_corrigidas.append('\n')
            continue  # Pula linhas em branco

        palavras = linha.split()
        linha_corrigida = []

        for palavra in palavras:
            # print("Palavra antes:", palavra)
            palavra_limpa = limpar_palavra(palavra).lower()
            # print("Palavra depois:", palavra_limpa)


            if len(palavra_limpa) >= 5 and not re.search(r'\d', palavra_limpa):  # verifica se a palavra tem 5 ou mais caracteres e não é apenas número

                if palavra_limpa not in dicionario_set:
                    candidatos = []
                    for p in dicionario_set:
                        # a distancia é calculada se tiver começar com a mesma letra
                        if p and palavra_limpa and p[0] == palavra_limpa[0]:
                            dist = levenshtein_distance(palavra_limpa, p)
                            if dist <= limite_distancia and len(p) == len(palavra_limpa): # Tem que ter o mesmo tamanho
                                candidatos.append((dist, p))

                    if candidatos: # tem algum candidato?
                        #print(palavra_limpa)
                        #print(candidatos)
                        # Priorizar palavras com acentuação
                        palavra_corrigida = min(candidatos, key=lambda x: (x[0], not tem_acento(x[1])))[1]
                        # print("TEORICA CORRECAO: ", palavra_corrigida)
                        # # Preservar a pontuação original
                        # palavra_com_pontuacao = palavra.replace(palavra_limpa, palavra_corrigida)
                        # print("Palavra com pontuação", palavra_com_pontuacao )
                        linha_corrigida.append(palavra_corrigida)
                        #print("Linha corrigida 1:", linha_corrigida)
                    else:
                        linha_corrigida.append(palavra_limpa)
                        #print("Linha corrigida 2:", linha_corrigida)
                else:
                    linha_corrigida.append(palavra_limpa)
                    #print("Linha corrigida 3:", linha_corrigida)
            else:
                linha_corrigida.append(palavra)
                #print("Linha corrigida 4:", linha_corrigida)
        # print("Linha corrigida", linha_corrigida)
        linhas_corrigidas.append(' '.join(linha_corrigida))

    caminho_arquivo_corrigido = os.path.join(diretorio_saida_caminho, os.path.basename(documento).replace('.txt', '_corrigido.txt'))

    with open(caminho_arquivo_corrigido, 'w', encoding='utf-8') as arquivo:
        arquivo.write('\n'.join(linhas_corrigidas))

Agora, chegou a hora de aplicar essa função nos documentos de texto. Portanto, vamos fazer conexão com o google drive para percorrer os arquivos no diretório em que se encontram.

In [ ]:
# percorrer todos os arquivos no diretório
for nome_arquivo in tqdm(os.listdir(FOLDER_TEXT), "Processando arquivos..."):
    if nome_arquivo.endswith(".txt"):
        documento = os.path.join(dir_arquivos_texto, nome_arquivo)
        corrige_texto(documento, dicionario, limite_distancia=2)

Processando arquivos...: 100%|█████████████████████████████████████████████████████| 76/76 [10:41:26<00:00, 506.40s/it]


Dessa forma, extraído o texto de todos os documentos da legislação da UFAM, podemos ir para a segunda parte para gerar a base de dados sintética de instruções.